In [1]:
import os
import sys
module_path = os.path.abspath(os.path.join('../../..'))
if module_path not in sys.path:
    sys.path.append(module_path)

In [2]:
print(module_path)

/Users/revilooliver/Documents/quantum_computing/research/pauli_sandwitching/cut4mitigation


In [3]:
# author: Ji Liu email: ji.liu@anl.gov

import itertools, numpy
import circuit_cutter
import mlrecon_methods as ml
import numpy as np
import mthree

import qiskit
from qiskit import *
from qiskit import QuantumCircuit, QuantumRegister, ClassicalRegister, Aer, execute, transpile

from qiskit.transpiler import PassManager

from qiskit.converters import circuit_to_dag
from qiskit.visualization import dag_drawer, plot_histogram
from qiskit.compiler import assemble

from qiskit.tools.monitor import job_monitor, backend_monitor, backend_overview

import qiskit.providers.aer.noise as noise
from qiskit.providers.aer.noise import NoiseModel

from utils.utils import filter_results, dict_to_list, H_distance, total_counts, norm_dict
from utils.vqe_utils import read_from_file, MeasureCircuit, find_commute_groups, evaluation, apply_checking_circuit
from mlrecon_methods import run_circuits, collect_fragment_circuits

In [4]:
qiskit.__qiskit_version__

{'qiskit-terra': '0.22.2', 'qiskit-aer': '0.11.1', 'qiskit-ignis': '0.7.1', 'qiskit-ibmq-provider': '0.19.2', 'qiskit': '0.39.2', 'qiskit-nature': '0.5.1', 'qiskit-finance': None, 'qiskit-optimization': None, 'qiskit-machine-learning': None}

In [5]:
numpy.set_printoptions(linewidth = 200)

simulation_backend = "qasm_simulator"

In [6]:
IBMQ.load_account()
provider = IBMQ.get_provider(hub='ibm-q-ornl', group='ornl', project='chm185')
provider.backends()

[<IBMQSimulator('ibmq_qasm_simulator') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_montreal') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_toronto') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_kolkata') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_mumbai') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_lima') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_belem') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_quito') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_guadalupe') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQSimulator('simulator_statevector') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQSimulator('simulator_mps') from IBMQ(hub='ibm-q-ornl', grou

In [7]:
device = provider.get_backend('ibm_auckland')
device

<IBMQBackend('ibm_auckland') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>

In [8]:
device.configuration().to_dict()['max_shots']

100000

In [9]:
from qiskit import IBMQ, Aer
from qiskit.providers.aer.noise import NoiseModel
noise_model = NoiseModel.from_backend(device, gate_error = False, thermal_relaxation= False)
print(noise_model)

NoiseModel:
  Basis gates: ['cx', 'id', 'reset', 'rz', 'sx', 'x']
  Instructions with noise: ['measure']
  Qubits with noise: [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26]
  Specific qubit errors: [('measure', (0,)), ('measure', (1,)), ('measure', (2,)), ('measure', (3,)), ('measure', (4,)), ('measure', (5,)), ('measure', (6,)), ('measure', (7,)), ('measure', (8,)), ('measure', (9,)), ('measure', (10,)), ('measure', (11,)), ('measure', (12,)), ('measure', (13,)), ('measure', (14,)), ('measure', (15,)), ('measure', (16,)), ('measure', (17,)), ('measure', (18,)), ('measure', (19,)), ('measure', (20,)), ('measure', (21,)), ('measure', (22,)), ('measure', (23,)), ('measure', (24,)), ('measure', (25,)), ('measure', (26,))]


In [10]:
noisy_simulator = provider.get_backend('ibmq_qasm_simulator')

In [11]:
front_layer = QuantumCircuit.from_qasm_file("qasm/vqe_HF_front.qasm")

In [12]:
mid_layer = QuantumCircuit.from_qasm_file("qasm/vqe_HF_mid.qasm")

In [13]:
end_layer = QuantumCircuit.from_qasm_file("qasm/vqe_HF_end.qasm")

In [14]:
orign_circuit = front_layer + mid_layer + end_layer

/var/folders/s4/3cvgkkn17hg628pzrzzjnhww0000gn/T/ipykernel_30974/743480212.py:1: DeprecationWarning: The QuantumCircuit.__add__() method is being deprecated.Use the compose() method which is more flexible w.r.t circuit register compatibility.
  orign_circuit = front_layer + mid_layer + end_layer


In [15]:
orign_circuit.draw()

┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐           │         »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘                     »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐                      »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘                      »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐                     »
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ ├────────────────┤└────────────┘                     »
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────────────────────────»
      └────────────────┘ └────────────────┘                                   »
q_8: ─────────────────────────────────────────────────────────────────────────»
                                                                              »
«        ┌────────────┐                                                      »
«q_0: ───┤ Rz(1.5641) ├──────────────────────────────────────────────────────»
«     ┌──┴────────────┴─┐┌─────────────┐                                     »
«q_1: ┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├─────────────────────────────────────»
«     └─────────────────┘├─────────────┴┐ ┌─────────────┐                    »
«q_2: ─────────■─────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├────────────────────»
«              │         └──────────────┘┌┴─────────────┴─┐ ┌──────────────┐ »
«q_3: ─────────■────────────────■────────┤ Ry(1.6108e-06) ├─┤ Rz(-0.12592) ├─»
«                               │        └────────────────┘┌┴──────────────┴┐»
«q_4: ──────────────────────────■────────────────■─────────┤ Ry(-8.148e-06) ├»
«                                                │         └────────────────┘»
«q_5: ───────────────────────────────────────────■─────────────────■─────────»
«                                                                  │         »
«q_6: ─────────────────────────────────────────────────────────────■─────────»
«                                                                            »
«q_7: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«q_8: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«                                                           
«q_0: ──────────────────────────────────────────────────────
«                                                           
«q_1: ──────────────────────────────────────────────────────
«                                                           
«q_2: ──────────────────────────────────────────────────────
«                                                           
«q_3: ──────────────────────────────────────────────────────
«        ┌────────────┐                                     
«q_4: ───┤ Rz(1.0747) ├─────────────────────────────────────
«     ┌──┴────────────┴─┐  ┌──────────────┐                 
«q_5: ┤ Ry(-8.6542e-06) ├──┤ Rz(-0.21554) ├─────────────────
«     └─────────────────┘┌─┴──────────────┴┐┌─────────────┐ 
«q_6: ─────────■─────────┤ Ry(-8.1451e-06) ├┤ Rz(0.25427) ├─
«              │         └┬────────────────┤├─────────────┴┐
«q_7: ─────────■──────────┤ Ry(-0.0044055) ├┤ Rz(0.010242) ├
«              

In [16]:
#checking circuit

In [17]:
phase_y_front = [6.827165202923369e-06,-1.6337052388981617e-05, -1.9504648473842978e-05, -4.583505307611714e-05, 6.10354282870864e-05, 5.965270087646158e-06, 9.312744374460134e-06, -0.0043764639879769]
phase_z_front = [1.7168697590535538, 1.5283131502120553, 1.8467840590281954, 1.9183949883797635, 1.8180451683566035, 1.8290020607579571,1.7186918294701956 ,0.0005809279491065732 ]
phase_y_end = [1.7553477050418194e-05, -5.2173015630282704e-06, 2.7300161977647244e-05, 1.6108036965651842e-06,-8.147972934398958e-06, -8.65422271101483e-06, -8.145059343430974e-06, -0.0044055233224810164]
phase_z_end = [1.5640736434660867, 0.8907239659216719, 0.8895530769206249, -0.12591739710453853, 1.0747017329581952, -0.21554369415117478, 0.25426734596118483, 0.010241971123548377]
x_front = [True, False, True, False, True, False, True, False]

In [18]:
qubit_id = 2
circuit = QuantumCircuit(9)
apply_checking_circuit(circuit, [qubit_id], [8], side = 'front', phase_y = phase_y_front[qubit_id], phase_z = phase_z_front[qubit_id], x = x_front[qubit_id])
circuit += orign_circuit
apply_checking_circuit(circuit, [qubit_id], [8], side = 'end', phase_y = phase_y_end[qubit_id], phase_z = phase_z_end[qubit_id])

/var/folders/s4/3cvgkkn17hg628pzrzzjnhww0000gn/T/ipykernel_30974/1304731301.py:4: DeprecationWarning: The QuantumCircuit.__iadd__() method is being deprecated. Use the compose() (potentially with the inplace=True argument) and tensor() methods which are more flexible w.r.t circuit register compatibility.
  circuit += orign_circuit


In [19]:
circuit.draw()

┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐    ┌─────────────┐  »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■──┤ Rz(-1.8468) ├──»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │  └─────────────┘  »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                   »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                   »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                   »
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼───────────────────»
      ┌─────┴───┴──────┐ ├────────────────┤└────────────┘ │                   »
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ └────────────────┘               │                   »
q_8: ───────┤ H ├─────────────────────────────────────────■───────────────────»
            └───┘                                                             »
«       ┌────────────┐                                                »
«q_0: ──┤ Rz(1.5641) ├────────────────────────────────────────────────»
«       └────────────┘                                                »
«q_1: ──────────────────────────────────────────────────────────────■─»
«     ┌────────────────┐┌───┐┌───┐┌─────────────────┐┌────────────┐ │ »
«q_2: ┤ Ry(1.9505e-05) ├┤ X ├┤ X ├┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■─»
«     └────────────────┘└───┘└───┘└─────────────────┘└────────────┘   »
«q_3: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_4: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_5: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_6: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_7: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_8: ────────────────────────────────────────────────────────────────»
«                                                                     »
«                                                                            »
«q_0: ───────────────────────────────────────────────────────────────────────»
«     ┌─────────────────┐┌─────────────┐                                     »
«q_1: ┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├─────────────────────────────────────»
«     └─────────────────┘├─────────────┴┐ ┌─────────────┐   ┌──────────────┐ »
«q_2: ─────────■─────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├───┤ Rz(-0.88955) ├─»
«              │         └──────────────┘┌┴─────────────┴─┐ ├──────────────┤ »
«q_3: ─────────■────────────────■────────┤ Ry(1.6108e-06) ├─┤ Rz(-0.12592) ├─»
«                               │        └────────────────┘┌┴──────────────┴┐»
«q_4: ──────────────────────────■────────────────■─────────┤ Ry(-8.148e-06) ├»
«                                                │         └────────────────┘»
«q_5: ───────────────────────────────────────────■─────────────────■─────────»
«                                                                  │         »
«q_6: ─────────────────────────────────────────────────────────────■─────────»
«                 

In [21]:
pauli_list = read_from_file('HF_hamiltonian.txt')
pauli_commute = find_commute_groups(pauli_list)

In [22]:
#generate individual measurment circuits that changes the basis
meas_qcs = []
for i in range(0, len(pauli_commute)):
    temp_qc = MeasureCircuit(pauli_commute[i], num_qubits = 8,num_qargs = 9)
    meas_qcs.append(temp_qc)
    print(temp_qc)

YXXYYXXY
     ┌──────────────┐
q_0: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_1: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_2: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_3: ┤ U(π/2,0,π/2) ├
     ├──────────────┤
q_4: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_5: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_6: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_7: ┤ U(π/2,0,π/2) ├
     └──────────────┘
q_8: ────────────────
                     
XXXXYXXY
      ┌────────────┐ 
q_0: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_1: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_2: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_3: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_4: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_5: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_6: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_7: ┤ U(π/2,0,π/2) ├
     └──────────────┘
q_8: ────────────────
                     
YXXYXXXX
     ┌──────────────┐
q_0: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_1: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_2: ─┤ U(π/2,0,π) ├─
     

In [23]:
circuit_list = []
for meas in meas_qcs:
    temp_circuit = circuit.copy()
    temp_circuit += meas
    circuit_list.append(temp_circuit)

/var/folders/s4/3cvgkkn17hg628pzrzzjnhww0000gn/T/ipykernel_30974/1717817760.py:4: DeprecationWarning: The QuantumCircuit.__iadd__() method is being deprecated. Use the compose() (potentially with the inplace=True argument) and tensor() methods which are more flexible w.r.t circuit register compatibility.
  temp_circuit += meas


In [24]:
circuit_list[-2].draw()

┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐    ┌─────────────┐  »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■──┤ Rz(-1.8468) ├──»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │  └─────────────┘  »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                   »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                   »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐ │                   »
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─┼───────────────────»
      ┌─────┴───┴──────┐ ├────────────────┤└────────────┘ │                   »
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ └────────────────┘               │                   »
q_8: ───────┤ H ├─────────────────────────────────────────■───────────────────»
            └───┘                                                             »
«       ┌────────────┐                                                »
«q_0: ──┤ Rz(1.5641) ├────────────────────────────────────────────────»
«       └────────────┘                                                »
«q_1: ──────────────────────────────────────────────────────────────■─»
«     ┌────────────────┐┌───┐┌───┐┌─────────────────┐┌────────────┐ │ »
«q_2: ┤ Ry(1.9505e-05) ├┤ X ├┤ X ├┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■─»
«     └────────────────┘└───┘└───┘└─────────────────┘└────────────┘   »
«q_3: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_4: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_5: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_6: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_7: ────────────────────────────────────────────────────────────────»
«                                                                     »
«q_8: ────────────────────────────────────────────────────────────────»
«                                                                     »
«                                                                            »
«q_0: ───────────────────────────────────────────────────────────────────────»
«     ┌─────────────────┐┌─────────────┐                                     »
«q_1: ┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├─────────────────────────────────────»
«     └─────────────────┘├─────────────┴┐ ┌─────────────┐   ┌──────────────┐ »
«q_2: ─────────■─────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├───┤ Rz(-0.88955) ├─»
«              │         └──────────────┘┌┴─────────────┴─┐ ├──────────────┤ »
«q_3: ─────────■────────────────■────────┤ Ry(1.6108e-06) ├─┤ Rz(-0.12592) ├─»
«                               │        └────────────────┘┌┴──────────────┴┐»
«q_4: ──────────────────────────■────────────────■─────────┤ Ry(-8.148e-06) ├»
«                                                │         └────────────────┘»
«q_5: ───────────────────────────────────────────■─────────────────■─────────»
«                                                                  │         »
«q_6: ─────────────────────────────────────────────────────────────■─────────»
«                 

In [26]:
cuts = [(circuit.qubits[2], 7),(circuit.qubits[2], 14)]

In [27]:
fragments_list = []
wire_path_map_list = []
for temp_qc in circuit_list:
    print(temp_qc)
    fragments, wire_path_map = circuit_cutter.cut_circuit(temp_qc, cuts)
    fragments_list.append(fragments)
    wire_path_map_list.append(wire_path_map)

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐    ┌─────────────┐  »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■──┤ Rz(-1.8468) ├──»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │  └─────────────┘  »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                   »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                   »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐    ┌─────────────┐  »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■──┤ Rz(-1.8468) ├──»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │  └─────────────┘  »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                   »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                   »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐    ┌─────────────┐  »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■──┤ Rz(-1.8468) ├──»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │  └─────────────┘  »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                   »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                   »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐    ┌─────────────┐  »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■──┤ Rz(-1.8468) ├──»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │  └─────────────┘  »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                   »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                   »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐    ┌─────────────┐  »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■──┤ Rz(-1.8468) ├──»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │  └─────────────┘  »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                   »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                   »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴

...

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐    ┌─────────────┐  »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■──┤ Rz(-1.8468) ├──»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │  └─────────────┘  »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                   »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                   »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐    ┌─────────────┐  »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■──┤ Rz(-1.8468) ├──»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │  └─────────────┘  »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                   »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                   »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐    ┌─────────────┐  »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■──┤ Rz(-1.8468) ├──»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │  └─────────────┘  »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                   »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                   »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐    ┌─────────────┐  »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■──┤ Rz(-1.8468) ├──»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │  └─────────────┘  »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                   »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                   »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴

            ┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐    ┌─────────────┐  »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■──┤ Rz(-1.8468) ├──»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘ │  └─────────────┘  »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────┼───────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐  │                   »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘  │                   »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────┼───────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴

In [28]:
print(wire_path_map_list[0])

{Qubit(QuantumRegister(9, 'q'), 0): ((0, Qubit(QuantumRegister(8, 'q'), 7)),), Qubit(QuantumRegister(9, 'q'), 1): ((0, Qubit(QuantumRegister(8, 'q'), 4)),), Qubit(QuantumRegister(9, 'q'), 2): ((1, Qubit(QuantumRegister(3, 'q'), 0)), (0, Qubit(QuantumRegister(8, 'q'), 3)), (1, Qubit(QuantumRegister(3, 'q'), 2))), Qubit(QuantumRegister(9, 'q'), 3): ((0, Qubit(QuantumRegister(8, 'q'), 0)),), Qubit(QuantumRegister(9, 'q'), 4): ((0, Qubit(QuantumRegister(8, 'q'), 6)),), Qubit(QuantumRegister(9, 'q'), 5): ((0, Qubit(QuantumRegister(8, 'q'), 2)),), Qubit(QuantumRegister(9, 'q'), 6): ((0, Qubit(QuantumRegister(8, 'q'), 1)),), Qubit(QuantumRegister(9, 'q'), 7): ((0, Qubit(QuantumRegister(8, 'q'), 5)),), Qubit(QuantumRegister(9, 'q'), 8): ((1, Qubit(QuantumRegister(3, 'q'), 1)),)}


In [29]:
total_variants = ml.fragment_variants(wire_path_map_list[0])

In [30]:
total_variants

24

In [31]:
shots = 10000 * total_variants

In [32]:
fragments_list[0][0].draw()

┌─────────────────┐   ┌────────────┐                                     »
q_0: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐                     »
q_1: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘                     »
q_2: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_3: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘           │         »
q_4: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_5: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌───────────┐  │                   »
q_6: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
            ├───┤        ├────────────────┤├───────────┴┐ │ ┌────────────────┐»
q_7: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            └───┘        └────────────────┘└────────────┘   └────────────────┘»
«                                        ┌────────────────┐┌──────────────┐»
«q_0: ─────────■────────────────■────────┤ Ry(1.6108e-06) ├┤ Rz(-0.12592) ├»
«              │                │        └────────────────┘└──────────────┘»
«q_1: ─────────┼────────────────┼──────────────────────────────────────────»
«              │                │                                          »
«q_2: ─────────┼────────────────┼──────────────────────────────────────────»
«              │                │         ┌──────────────┐ ┌─────────────┐ »
«q_3: ─────────■────────────────┼─────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├─»
«     ┌─────────────────┐       │         ├─────────────┬┘ └┬────────────┤ »
«q_4: ┤ Ry(-5.2173e-06) ├───────┼─────────┤ Rz(0.89072) ├───┤ U(π/2,0,π) ├─»
«     └─────────────────┘       │         └─────────────┘   └────────────┘ »
«q_5: ──────────────────────────┼──────────────────────────────────────────»
«                               │                                          »
«q_6: ──────────────────────────■──────────────────────────────────────────»
«        ┌────────────┐  ┌──────────────┐                                  »
«q_7: ───┤ Rz(1.5641) ├──┤ U(π/2,0,π/2) ├──────────────────────────────────»
«        └────────────┘  └──────────────┘                                  »
«     ┌──────────────┐                                                   »
«q_0: ┤ U(π/2,0,π/2) ├───────────────────────────────────────────────────»
«     └──────────────┘                                ┌─────────────────┐»
«q_1: ────────────────────────■───────────────■───────┤ Ry(-8.1451e-06) ├»
«                             │               │       ├─────────────────┤»
«q_2: ───────■────────────────■───────────────┼───────┤ Ry(-8.6542e-06) ├»
«            │                                │       └─────────────────┘»
«q_3: ───────┼────────────────────────────────┼──────────────────────────»
«            │                                │                          »
«q_4: ───────┼────────────────────────────────┼──────────────────────────»
«            │                                │        ┌────────────────┐»
«q_5: ───────┼────────────────────────────────■────────┤ Ry(-0.0044055) ├»
«            │        ┌────────────────┐┌────────────┐ └┬──────────────┬┘»
«q_6: ───────■────────┤ Ry(-8.148e-06) ├┤ Rz(1.0747) ├──┤ U(π/2,0,π/2) ├─»
«                     └────────────────┘└────────────┘  └──────────────┘ »
«q_7: ───────────────────────────────────────────────────────────────────»
«                                                                        »
«                                     
«q_0: ────────────────

In [33]:
fragment_cuts_list = []
for index in range(0, len(fragments_list)):
    for idx, fragment in enumerate(fragments_list[index]):
        print(f"fragment {idx}:")
        print(fragment)
        print()
    fragment_cuts = ml.fragment_cuts(wire_path_map_list[index])
    fragment_cuts_list.append(fragment_cuts)


fragment 0:
     ┌─────────────────┐   ┌────────────┐                                     »
q_0: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐                     »
q_1: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘                     »
q_2: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_3: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘           │         »
q_4: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_5: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├──

     ┌─────────────────┐   ┌────────────┐                                     »
q_0: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐                     »
q_1: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘                     »
q_2: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_3: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘           │         »
q_4: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_5: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├──────────────

     ┌─────────────────┐   ┌────────────┐                                     »
q_0: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐                     »
q_1: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘                     »
q_2: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_3: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘           │         »
q_4: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_5: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├──────────────

     ┌─────────────────┐   ┌────────────┐                                     »
q_0: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐                     »
q_1: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘                     »
q_2: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_3: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘           │         »
q_4: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_5: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├──────────────

     ┌─────────────────┐   ┌────────────┐                                     »
q_0: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐                     »
q_1: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘                     »
q_2: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_3: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘           │         »
q_4: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_5: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├──────────────

...

     ┌─────────────────┐   ┌────────────┐                                     »
q_0: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐                     »
q_1: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘                     »
q_2: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_3: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘           │         »
q_4: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_5: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├──────────────

     ┌─────────────────┐   ┌────────────┐                                     »
q_0: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐                     »
q_1: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘                     »
q_2: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_3: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘           │         »
q_4: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_5: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├──────────────

          ┌───┐      ┌─────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ─────┤ X ├──────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■─┤ Rz(-1.8468) ├»
          ├───┤      └─────────────────┘└────────────┘ │ └─────────────┘»
q_1: ─────┤ H ├────────────────────────────────────────■────────■───────»
     ┌────┴───┴─────┐ ┌───────────────┐                         │       »
q_2: ┤ Rz(-0.88955) ├─┤ Ry(-2.73e-05) ├─────────────────────────■───────»
     └──────────────┘ └───────────────┘                                 »
«     ┌────────────────┐     ┌───┐                     
«q_0: ┤ Ry(1.9505e-05) ├─────┤ X ├─────────────────────
«     └─────┬───┬──────┘     └───┘                     
«q_1: ──────┤ H ├──────────────────────────────────────
«      ┌────┴───┴─────┐ ┌─────────────┐┌──────────────┐
«q_2: ─┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├┤ U(π/2,0,π/2) ├
«      └──────────────┘ └─────────────┘└──────────────┘

fragment 0:
     ┌─────────────────┐   ┌────────────┐                                    

     ┌─────────────────┐   ┌────────────┐                                     »
q_0: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐                     »
q_1: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘                     »
q_2: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_3: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘           │         »
q_4: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_5: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├──────────────

     ┌─────────────────┐   ┌────────────┐                                     »
q_0: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐                     »
q_1: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘                     »
q_2: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_3: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘           │         »
q_4: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_5: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├──────────────

In [34]:
print(fragment_cuts_list[-1])

[{'prep': 1, 'meas': 1}, {'prep': 1, 'meas': 1}]


In [35]:
wire_path_map

{Qubit(QuantumRegister(9, 'q'), 0): ((0, Qubit(QuantumRegister(8, 'q'), 7)),),
 Qubit(QuantumRegister(9, 'q'), 1): ((0, Qubit(QuantumRegister(8, 'q'), 4)),),
 Qubit(QuantumRegister(9, 'q'), 2): ((1, Qubit(QuantumRegister(3, 'q'), 0)),
  (0, Qubit(QuantumRegister(8, 'q'), 3)),
  (1, Qubit(QuantumRegister(3, 'q'), 2))),
 Qubit(QuantumRegister(9, 'q'), 3): ((0, Qubit(QuantumRegister(8, 'q'), 0)),),
 Qubit(QuantumRegister(9, 'q'), 4): ((0, Qubit(QuantumRegister(8, 'q'), 6)),),
 Qubit(QuantumRegister(9, 'q'), 5): ((0, Qubit(QuantumRegister(8, 'q'), 2)),),
 Qubit(QuantumRegister(9, 'q'), 6): ((0, Qubit(QuantumRegister(8, 'q'), 1)),),
 Qubit(QuantumRegister(9, 'q'), 7): ((0, Qubit(QuantumRegister(8, 'q'), 5)),),
 Qubit(QuantumRegister(9, 'q'), 8): ((1, Qubit(QuantumRegister(3, 'q'), 1)),)}

In [36]:
num_fragments = len(fragments)
num_fragments

2

In [37]:
num_tomo_circuits = len(meas_qcs)
num_tomo_circuits

76

In [38]:
fragments[0].draw()

┌─────────────────┐   ┌────────────┐                                     »
q_0: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌────────────┐                     »
q_1: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└────────────┘                     »
q_2: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘┌──┴───────────┴──┐┌────────────┐                     »
q_3: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘           │         »
q_4: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_5: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌───────────┐  │                   »
q_6: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──┼───────────────────»
            ├───┤        ├────────────────┤├───────────┴┐ │ ┌────────────────┐»
q_7: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            └───┘        └────────────────┘└────────────┘   └────────────────┘»
«                                      ┌────────────────┐┌──────────────┐   »
«q_0: ─────────■───────────────■───────┤ Ry(1.6108e-06) ├┤ Rz(-0.12592) ├───»
«              │               │       └────────────────┘└──────────────┘   »
«q_1: ─────────┼───────────────┼────────────────────────────────────────────»
«              │               │                                            »
«q_2: ─────────┼───────────────┼──────────────────────────────────────────■─»
«              │               │        ┌──────────────┐ ┌─────────────┐  │ »
«q_3: ─────────■───────────────┼────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├──┼─»
«     ┌─────────────────┐      │        ├─────────────┬┘ └─────────────┘  │ »
«q_4: ┤ Ry(-5.2173e-06) ├──────┼────────┤ Rz(0.89072) ├───────────────────┼─»
«     └─────────────────┘      │        └─────────────┘                   │ »
«q_5: ─────────────────────────┼──────────────────────────────────────────┼─»
«                              │                                          │ »
«q_6: ─────────────────────────■──────────────────────────────────────────■─»
«        ┌────────────┐  ┌────────────┐                                     »
«q_7: ───┤ Rz(1.5641) ├──┤ U(π/2,0,π) ├─────────────────────────────────────»
«        └────────────┘  └────────────┘                                     »
«                                                                        
«q_0: ───────────────────────────────────────────────────────────────────
«                                     ┌─────────────────┐┌─────────────┐ 
«q_1: ────────■───────────────■───────┤ Ry(-8.1451e-06) ├┤ Rz(0.25427) ├─
«             │               │       ├─────────────────┤├─────────────┴┐
«q_2: ────────■───────────────┼───────┤ Ry(-8.6542e-06) ├┤ Rz(-0.21554) ├
«                             │       └─────────────────┘└──────────────┘
«q_3: ────────────────────────┼──────────────────────────────────────────
«                             │                                          
«q_4: ────────────────────────┼──────────────────────────────────────────
«                             │        ┌────────────────┐┌──────────────┐
«q_5: ────────────────────────■────────┤ Ry(-0.0044055) ├┤ Rz(0.010242) ├
«     ┌────────────────┐┌────────────┐ └────────────────┘└──────────────┘
«q_6: ┤ Ry(-8.148e-06) ├┤ Rz(1.0747) ├───────────────────────────────────
«     └────────────────┘└────────────┘                                   
«q_7: ───────────────────────────────────────────────────────────────────
«

In [39]:
fragments[1].draw()

┌───┐      ┌─────────────────┐┌────────────┐   ┌─────────────┐»
q_0: ─────┤ X ├──────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─■─┤ Rz(-1.8468) ├»
          ├───┤      └─────────────────┘└────────────┘ │ └─────────────┘»
q_1: ─────┤ H ├────────────────────────────────────────■────────■───────»
     ┌────┴───┴─────┐ ┌───────────────┐                         │       »
q_2: ┤ Rz(-0.88955) ├─┤ Ry(-2.73e-05) ├─────────────────────────■───────»
     └──────────────┘ └───────────────┘                                 »
«     ┌────────────────┐     ┌───┐     
«q_0: ┤ Ry(1.9505e-05) ├─────┤ X ├─────
«     └─────┬───┬──────┘     └───┘     
«q_1: ──────┤ H ├──────────────────────
«      ┌────┴───┴─────┐ ┌─────────────┐
«q_2: ─┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├
«      └──────────────┘ └─────────────┘

In [40]:
hardware_index = 0

In [41]:
print(shots)

240000


In [42]:
tomography_circuits = []
for idx in range(0, len(fragments_list)):
    fragments = fragments_list[idx]
    wire_path_map = wire_path_map_list[idx]
    temp_frag_circuits = [0] * len(fragments)
    for i in range(0, len(fragments)):
        if i == hardware_index:
            temp_frag_circuits[i] = collect_fragment_circuits(fragments[i], i, wire_path_map,
                                         shots = shots // total_variants,
                                         tomography_backend = simulation_backend)
        else:
            temp_frag_circuits[i] = collect_fragment_circuits(fragments[i], i, wire_path_map,
                                         shots = shots // total_variants,
                                         tomography_backend = simulation_backend)
    tomography_circuits.append(temp_frag_circuits)

In [43]:
#contains 34 basis
len(tomography_circuits)

76

In [44]:
#contains two fragments
len(tomography_circuits[0])

2

In [45]:
len(tomography_circuits[0][1])

1

In [46]:
#tomography circuits
len(tomography_circuits[0][1][0])

12

In [47]:
multi_exp_circuits = [[],[]]
for i in range(0, len(tomography_circuits)):
    #for each basis collect the three fragments:
    for j in range(0, num_fragments):
        fragment_circ = tomography_circuits[i][j][0]
        multi_exp_circuits[j] += fragment_circ

In [48]:
#[9,8,11,14,13,12,10,7]
#74306215
#[14,10,12,11,8,7,13,9]

In [49]:
multi_exp_circuits[hardware_index][-200].draw()

░ ┌─────────────────┐   ┌────────────┐  »
   q_0: ────────────────────░─┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──»
                            ░ └──────┬───┬──────┘ ┌─┴────────────┴─┐»
   q_1: ────────────────────░────────┤ X ├────────┤ Ry(9.3127e-06) ├»
                            ░  ┌─────┴───┴──────┐ └─┬───────────┬──┘»
   q_2: ────────────────────░──┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├───»
        ┌─────────────────┐ ░  └─────┬───┬──────┘┌──┴───────────┴──┐»
   q_3: ┤ U3(-1.9106,π,0) ├─░────────┤ X ├───────┤ Ry(-1.9505e-05) ├»
        └─────────────────┘ ░ ┌──────┴───┴──────┐└──┬────────────┬─┘»
   q_4: ────────────────────░─┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──»
                            ░ └┬────────────────┤ ┌─┴────────────┴─┐»
   q_5: ────────────────────░──┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├»
                            ░  └─────┬───┬──────┘ ├────────────────┤»
   q_6: ────────────────────░────────┤ X ├────────┤ Ry(6.1035e-05) ├»
                            ░        ├───┤        ├────────────────┤»
   q_7: ────────────────────░────────┤ X ├────────┤ Ry(6.8272e-06) ├»
                            ░        └───┘        └────────────────┘»
c118_0: ════════════════════════════════════════════════════════════»
                                                                    »
c118_1: ════════════════════════════════════════════════════════════»
                                                                    »
c118_2: ════════════════════════════════════════════════════════════»
                                                                    »
c118_3: ════════════════════════════════════════════════════════════»
                                                                    »
c118_4: ════════════════════════════════════════════════════════════»
                                                                    »
c118_5: ════════════════════════════════════════════════════════════»
                                                                    »
c118_6: ════════════════════════════════════════════════════════════»
                                                                    »
c118_7: ════════════════════════════════════════════════════════════»
                                                                    »
«                                                                            »
«   q_0: ────────────────────────────────────────────■───────────────■───────»
«        ┌────────────┐                              │               │       »
«   q_1: ┤ Rz(1.7187) ├──────────────────────────────┼───────────────┼───────»
«        └────────────┘                              │               │       »
«   q_2: ────────────────────────────────────────────┼───────────────┼───────»
«        ┌────────────┐                              │               │       »
«   q_3: ┤ Rz(1.8468) ├───────────■──────────────────■───────────────┼───────»
«        └────────────┘           │         ┌─────────────────┐      │       »
«   q_4: ───────────────■─────────■─────────┤ Ry(-5.2173e-06) ├──────┼───────»
«                       │                   └─────────────────┘      │       »
«   q_5: ───────────────┼────────────────────────────────────────────┼───────»
«        ┌───────────┐  │                                            │       »
«   q_6: ┤ Rz(1.818) ├──┼────────────────────────────────────────────■───────»
«        ├───────────┴┐ │ ┌────────────────┐   ┌────────────┐  ┌────────────┐»
«   q_7: ┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├───┤ Rz(1.5641) ├──┤ U(π/2,0,π) ├»
«        └────────────┘   └────────────────┘   └────────────┘  └────────────┘»
«c118_0: ════════════════════════════════════════════════════════════════════»
«                                                                            »
«c118_1: ════════════════════════════════════════════════════════════════════»
«                                                                            »
«c118_2: ══════════════════════════════════════════════════

In [61]:
len(multi_exp_circuits[0])

408

In [74]:
frag_datas = [0] * num_fragments
for i in range(0, num_fragments):
    if i == hardware_index:
        frag_datas[i] = run_circuits(multi_exp_circuits[i], initial_layout = [14,10,12,11,8,7,13,9],
                                     backend = device, shots = shots // total_variants, 
                                     optimization_level = 3, monitor_jobs = True)
    else:
        frag_datas[i] = run_circuits(multi_exp_circuits[i], initial_layout = None,
                                     backend = simulation_backend, shots = shots // total_variants,
                                     optimization_level = 3, monitor_jobs = True, noise_model = None)
       

jobset_id:  bd4f9568aa174039a7b2c65cf26e765a-1670515827425882
job_id:  5960e209-cd07-43cc-b249-ed46bc89ac6e
Job Status: job has successfully run


In [ ]:
# from qiskit.providers.ibmq.managed import IBMQJobManager
# job_manager = IBMQJobManager()

In [ ]:
# job_set = job_manager.retrieve_job_set(job_set_id='973c2fdceaf547389a770d19aad463d8-1669966038684177', provider=provider)

In [ ]:
# managed_results = job_set.results()

In [ ]:
# frag_datas1_copy = frag_datas[1].copy()

In [75]:
frag_datas[0] = [frag_datas[0][0].combine_results()]

In [76]:
# frag_datas[0] = run_circuits(multi_exp_circuits[0], initial_layout = None,
#                              backend = simulation_backend, shots = shots // total_variants,
#                              optimization_level = 3, monitor_jobs = True, noise_model = None)

In [77]:
frag_datas[0][0].results[0].header.name

"(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z'))"

In [78]:
num_tomo_circuits

76

In [79]:
test = [[], []]

In [80]:
results_list = [[], []]
counts_list = [[], []] 
for i in range(0, num_fragments): 
    for j in range(0, num_tomo_circuits):
        start_idx = j * 12
        end_idx = (j + 1) * 12
        results_list[i].append(frag_datas[i][0].results[start_idx : end_idx])
        counts_list[i].append(frag_datas[i][0].get_counts()[start_idx : end_idx])


In [81]:
from mlrecon_methods import organize_tomography_data_from_list
organized_data = []
for i in range(0, num_tomo_circuits):
    frag_data = []
    frag_targets = ml.identify_frag_targets(wire_path_map_list[i])
    for j in range(0, num_fragments):
        frag_data.append(organize_tomography_data_from_list(results_list[j][i], counts_list[j][i],
                                              frag_targets[j].get("prep"),
                                              frag_targets[j].get("meas"),
                                              prep_basis = "SIC", extra_qc = []))
    organized_data.append(frag_data)

(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0',) ('Z',) [3] [3]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'X', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'X', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'X', 'Z', 'Z', 'Z', 'Z')) ('S0',) ('X',) [3] [3]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Y', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Y', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Y', 'Z', 'Z', 'Z', 'Z')) ('S0',) ('Y',) [3] [3]
(('S0', 'S0', 'S0', 'S1', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0

(('S0', 'S0', 'S2'), ('Z', 'Z', 'Z')) ('S2',) ('Z',) [2] [0]
(('S0', 'S0', 'S2'), ('X', 'Z', 'Z')) ('S0', 'S0', 'S2') ('X', 'Z', 'Z')
(('S0', 'S0', 'S2'), ('X', 'Z', 'Z')) ('S2',) ('X',) [2] [0]
(('S0', 'S0', 'S2'), ('Y', 'Z', 'Z')) ('S0', 'S0', 'S2') ('Y', 'Z', 'Z')
(('S0', 'S0', 'S2'), ('Y', 'Z', 'Z')) ('S2',) ('Y',) [2] [0]
(('S0', 'S0', 'S3'), ('Z', 'Z', 'Z')) ('S0', 'S0', 'S3') ('Z', 'Z', 'Z')
(('S0', 'S0', 'S3'), ('Z', 'Z', 'Z')) ('S3',) ('Z',) [2] [0]
(('S0', 'S0', 'S3'), ('X', 'Z', 'Z')) ('S0', 'S0', 'S3') ('X', 'Z', 'Z')
(('S0', 'S0', 'S3'), ('X', 'Z', 'Z')) ('S3',) ('X',) [2] [0]
(('S0', 'S0', 'S3'), ('Y', 'Z', 'Z')) ('S0', 'S0', 'S3') ('Y', 'Z', 'Z')
(('S0', 'S0', 'S3'), ('Y', 'Z', 'Z')) ('S3',) ('Y',) [2] [0]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z',

(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'X', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'X', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'X', 'Z', 'Z', 'Z', 'Z')) ('S0',) ('X',) [3] [3]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Y', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Y', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Y', 'Z', 'Z', 'Z', 'Z')) ('S0',) ('Y',) [3] [3]
(('S0', 'S0', 'S0', 'S1', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S1', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S1', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S1',) ('Z',) [3] [3]
(('S0', 'S0', 'S0', 'S1', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'X', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0

In [82]:
for final_bits, fixed_bit_data in frag_data[0].items():
    prep_meas_states, state_counts = zip(*fixed_bit_data.items())
    prep_labels, meas_labels = zip(*prep_meas_states)
    prep_qubit_num = len(prep_labels[0])
    meas_qubit_num = len(meas_labels[0])
    print(prep_qubit_num)

1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


In [83]:
len(organized_data)

76

In [84]:
recombined_lists = []
filtered_recombined_lists = []
norm_filtered_lists = []
for i in range(0, num_tomo_circuits):
    direct_models = ml.direct_fragment_model(organized_data[i])
    likely_models = ml.maximum_likelihood_model(direct_models)

    direct_recombined_dist = ml.recombine_fragment_models(direct_models, wire_path_map_list[i])
    likely_recombined_dist = ml.recombine_fragment_models(likely_models, wire_path_map_list[i])
    recombined_lists.append(likely_recombined_dist)
    filtered_recombined_lists.append(filter_results(likely_recombined_dist, [0]))
    norm_filtered_lists.append(norm_dict(filter_results(likely_recombined_dist, [0])))

{'0000000': {(('S0',), ('Zp',)): 3, (('S0',), ('Zm',)): 74, (('S0',), ('Xp',)): 41, (('S0',), ('Xm',)): 40, (('S0',), ('Yp',)): 33, (('S0',), ('Ym',)): 37, (('S1',), ('Zp',)): 55, (('S1',), ('Zm',)): 35, (('S1',), ('Xp',)): 11, (('S1',), ('Xm',)): 56, (('S1',), ('Yp',)): 51, (('S1',), ('Ym',)): 18, (('S2',), ('Zp',)): 54, (('S2',), ('Zm',)): 13, (('S2',), ('Xp',)): 52, (('S2',), ('Xm',)): 34, (('S2',), ('Yp',)): 8, (('S2',), ('Ym',)): 67, (('S3',), ('Zp',)): 40, (('S3',), ('Zm',)): 22, (('S3',), ('Xp',)): 65, (('S3',), ('Xm',)): 14, (('S3',), ('Yp',)): 66, (('S3',), ('Ym',)): 23}, '0000001': {(('S0',), ('Zp',)): 3, (('S0',), ('Zm',)): 64, (('S0',), ('Xp',)): 38, (('S0',), ('Xm',)): 40, (('S0',), ('Yp',)): 46, (('S0',), ('Ym',)): 34, (('S1',), ('Zp',)): 51, (('S1',), ('Zm',)): 24, (('S1',), ('Xp',)): 11, (('S1',), ('Xm',)): 78, (('S1',), ('Yp',)): 54, (('S1',), ('Ym',)): 25, (('S2',), ('Zp',)): 54, (('S2',), ('Zm',)): 25, (('S2',), ('Xp',)): 34, (('S2',), ('Xm',)): 34, (('S2',), ('Yp',)

{'11': {(('S0',), ('Zp',)): 5036, (('S0',), ('Xp',)): 2440, (('S0',), ('Xm',)): 2605, (('S0',), ('Ym',)): 2464, (('S0',), ('Yp',)): 2451, (('S1',), ('Zp',)): 1632, (('S1',), ('Xp',)): 838, (('S1',), ('Xm',)): 820, (('S1',), ('Yp',)): 862, (('S1',), ('Ym',)): 847, (('S2',), ('Zp',)): 1657, (('S2',), ('Xp',)): 832, (('S2',), ('Xm',)): 824, (('S2',), ('Yp',)): 840, (('S2',), ('Ym',)): 863, (('S3',), ('Zp',)): 1669, (('S3',), ('Xm',)): 816, (('S3',), ('Xp',)): 808, (('S3',), ('Ym',)): 872, (('S3',), ('Yp',)): 823, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '01': {(('S0',), ('Zp',)): 4964, (('S0',), ('Xp',)): 2553, (('S0',), ('Xm',)): 2402, (('S0',), ('Yp',)): 2565, (('S0',), ('Ym',)): 2520, (('S1',), ('Zp',)): 1687, (('S1',), ('Xp',)): 839, (('S1',), ('Xm',)): 882, (('S1',), ('Yp',)): 855, (('S1',), ('Ym',)): 839, (('S2',), ('Zp',)): 1629, (('S2',), ('Xp',)): 827, (('S2',), ('Xm',)): 822, (('S2',), ('Ym',)): 867, (('S2',), ('Yp',)): 885, ((

{'0000001': {(('S0',), ('Zp',)): 3, (('S0',), ('Zm',)): 89, (('S0',), ('Xp',)): 34, (('S0',), ('Xm',)): 43, (('S0',), ('Yp',)): 42, (('S0',), ('Ym',)): 42, (('S1',), ('Zp',)): 49, (('S1',), ('Zm',)): 30, (('S1',), ('Xp',)): 8, (('S1',), ('Xm',)): 77, (('S1',), ('Yp',)): 58, (('S1',), ('Ym',)): 13, (('S2',), ('Zp',)): 45, (('S2',), ('Zm',)): 20, (('S2',), ('Xp',)): 54, (('S2',), ('Xm',)): 24, (('S2',), ('Yp',)): 4, (('S2',), ('Ym',)): 78, (('S3',), ('Zp',)): 57, (('S3',), ('Zm',)): 28, (('S3',), ('Xp',)): 69, (('S3',), ('Xm',)): 11, (('S3',), ('Yp',)): 61, (('S3',), ('Ym',)): 18}, '0001001': {(('S0',), ('Zp',)): 3, (('S0',), ('Zm',)): 87, (('S0',), ('Xp',)): 37, (('S0',), ('Xm',)): 32, (('S0',), ('Yp',)): 38, (('S0',), ('Ym',)): 35, (('S1',), ('Zp',)): 47, (('S1',), ('Zm',)): 24, (('S1',), ('Xp',)): 10, (('S1',), ('Xm',)): 60, (('S1',), ('Yp',)): 69, (('S1',), ('Ym',)): 28, (('S2',), ('Zp',)): 58, (('S2',), ('Zm',)): 28, (('S2',), ('Xp',)): 48, (('S2',), ('Xm',)): 43, (('S2',), ('Yp',))

{'11': {(('S0',), ('Zp',)): 5007, (('S0',), ('Xm',)): 2488, (('S0',), ('Xp',)): 2501, (('S0',), ('Ym',)): 2565, (('S0',), ('Yp',)): 2461, (('S1',), ('Zp',)): 1663, (('S1',), ('Xp',)): 851, (('S1',), ('Xm',)): 879, (('S1',), ('Ym',)): 810, (('S1',), ('Yp',)): 825, (('S2',), ('Zp',)): 1705, (('S2',), ('Xm',)): 809, (('S2',), ('Xp',)): 841, (('S2',), ('Yp',)): 794, (('S2',), ('Ym',)): 880, (('S3',), ('Zp',)): 1649, (('S3',), ('Xp',)): 833, (('S3',), ('Xm',)): 839, (('S3',), ('Ym',)): 813, (('S3',), ('Yp',)): 804, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '01': {(('S0',), ('Zp',)): 4993, (('S0',), ('Xp',)): 2496, (('S0',), ('Xm',)): 2515, (('S0',), ('Ym',)): 2538, (('S0',), ('Yp',)): 2436, (('S1',), ('Zp',)): 1643, (('S1',), ('Xp',)): 855, (('S1',), ('Xm',)): 813, (('S1',), ('Ym',)): 822, (('S1',), ('Yp',)): 785, (('S2',), ('Zp',)): 1652, (('S2',), ('Xp',)): 866, (('S2',), ('Xm',)): 815, (('S2',), ('Yp',)): 820, (('S2',), ('Ym',)): 867, ((

{'0001101': {(('S0',), ('Zp',)): 2, (('S0',), ('Zm',)): 8, (('S0',), ('Xp',)): 5, (('S0',), ('Xm',)): 8, (('S0',), ('Yp',)): 6, (('S0',), ('Ym',)): 4, (('S1',), ('Zp',)): 11, (('S1',), ('Zm',)): 2, (('S1',), ('Xm',)): 8, (('S1',), ('Yp',)): 5, (('S1',), ('Ym',)): 2, (('S2',), ('Zp',)): 5, (('S2',), ('Zm',)): 3, (('S2',), ('Xp',)): 13, (('S2',), ('Xm',)): 1, (('S2',), ('Yp',)): 4, (('S2',), ('Ym',)): 5, (('S3',), ('Zp',)): 3, (('S3',), ('Zm',)): 3, (('S3',), ('Xp',)): 6, (('S3',), ('Xm',)): 2, (('S3',), ('Yp',)): 7, (('S3',), ('Ym',)): 2, (('S1',), ('Xp',)): 0}, '0001110': {(('S0',), ('Zp',)): 1, (('S0',), ('Zm',)): 6, (('S0',), ('Xp',)): 4, (('S0',), ('Xm',)): 3, (('S0',), ('Yp',)): 1, (('S0',), ('Ym',)): 8, (('S1',), ('Zp',)): 4, (('S1',), ('Zm',)): 1, (('S1',), ('Xp',)): 1, (('S1',), ('Xm',)): 8, (('S1',), ('Yp',)): 6, (('S1',), ('Ym',)): 2, (('S2',), ('Zp',)): 6, (('S2',), ('Zm',)): 3, (('S2',), ('Xp',)): 9, (('S2',), ('Xm',)): 3, (('S2',), ('Yp',)): 2, (('S2',), ('Ym',)): 4, (('S3'

...

{'0000000': {(('S0',), ('Zp',)): 5, (('S0',), ('Zm',)): 83, (('S0',), ('Xp',)): 46, (('S0',), ('Xm',)): 49, (('S0',), ('Yp',)): 47, (('S0',), ('Ym',)): 52, (('S1',), ('Zp',)): 51, (('S1',), ('Zm',)): 13, (('S1',), ('Xp',)): 6, (('S1',), ('Xm',)): 90, (('S1',), ('Yp',)): 30, (('S1',), ('Ym',)): 47, (('S2',), ('Zp',)): 49, (('S2',), ('Zm',)): 15, (('S2',), ('Xp',)): 54, (('S2',), ('Xm',)): 15, (('S2',), ('Yp',)): 14, (('S2',), ('Ym',)): 62, (('S3',), ('Zp',)): 49, (('S3',), ('Zm',)): 30, (('S3',), ('Xp',)): 64, (('S3',), ('Xm',)): 30, (('S3',), ('Yp',)): 83, (('S3',), ('Ym',)): 9}, '0000001': {(('S0',), ('Zp',)): 1, (('S0',), ('Zm',)): 69, (('S0',), ('Xp',)): 36, (('S0',), ('Xm',)): 35, (('S0',), ('Yp',)): 32, (('S0',), ('Ym',)): 36, (('S1',), ('Zp',)): 55, (('S1',), ('Zm',)): 36, (('S1',), ('Xp',)): 2, (('S1',), ('Xm',)): 79, (('S1',), ('Yp',)): 34, (('S1',), ('Ym',)): 34, (('S2',), ('Zp',)): 66, (('S2',), ('Zm',)): 24, (('S2',), ('Xp',)): 51, (('S2',), ('Xm',)): 24, (('S2',), ('Yp',)):

{'0000000': {(('S0',), ('Zp',)): 3, (('S0',), ('Zm',)): 86, (('S0',), ('Xp',)): 42, (('S0',), ('Xm',)): 37, (('S0',), ('Yp',)): 35, (('S0',), ('Ym',)): 43, (('S1',), ('Zp',)): 55, (('S1',), ('Zm',)): 32, (('S1',), ('Xp',)): 7, (('S1',), ('Xm',)): 76, (('S1',), ('Yp',)): 65, (('S1',), ('Ym',)): 25, (('S2',), ('Zp',)): 48, (('S2',), ('Zm',)): 21, (('S2',), ('Xp',)): 46, (('S2',), ('Xm',)): 38, (('S2',), ('Yp',)): 11, (('S2',), ('Ym',)): 92, (('S3',), ('Zp',)): 38, (('S3',), ('Zm',)): 37, (('S3',), ('Xp',)): 59, (('S3',), ('Xm',)): 10, (('S3',), ('Yp',)): 67, (('S3',), ('Ym',)): 18}, '0000001': {(('S0',), ('Zp',)): 2, (('S0',), ('Zm',)): 80, (('S0',), ('Xp',)): 34, (('S0',), ('Xm',)): 37, (('S0',), ('Yp',)): 34, (('S0',), ('Ym',)): 37, (('S1',), ('Zp',)): 55, (('S1',), ('Zm',)): 33, (('S1',), ('Xp',)): 10, (('S1',), ('Xm',)): 88, (('S1',), ('Yp',)): 58, (('S1',), ('Ym',)): 28, (('S2',), ('Zp',)): 65, (('S2',), ('Zm',)): 31, (('S2',), ('Xp',)): 41, (('S2',), ('Xm',)): 46, (('S2',), ('Yp',)

{'01': {(('S0',), ('Zp',)): 5034, (('S0',), ('Xm',)): 2487, (('S0',), ('Xp',)): 2498, (('S0',), ('Yp',)): 2539, (('S0',), ('Ym',)): 2536, (('S1',), ('Zp',)): 1728, (('S1',), ('Xp',)): 850, (('S1',), ('Xm',)): 881, (('S1',), ('Ym',)): 860, (('S1',), ('Yp',)): 817, (('S2',), ('Zp',)): 1649, (('S2',), ('Xm',)): 871, (('S2',), ('Xp',)): 777, (('S2',), ('Ym',)): 825, (('S2',), ('Yp',)): 879, (('S3',), ('Zp',)): 1642, (('S3',), ('Xp',)): 830, (('S3',), ('Xm',)): 840, (('S3',), ('Ym',)): 846, (('S3',), ('Yp',)): 805, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '11': {(('S0',), ('Zp',)): 4966, (('S0',), ('Xm',)): 2509, (('S0',), ('Xp',)): 2506, (('S0',), ('Ym',)): 2377, (('S0',), ('Yp',)): 2548, (('S1',), ('Zp',)): 1725, (('S1',), ('Xp',)): 792, (('S1',), ('Xm',)): 848, (('S1',), ('Ym',)): 831, (('S1',), ('Yp',)): 860, (('S2',), ('Zp',)): 1646, (('S2',), ('Xm',)): 809, (('S2',), ('Xp',)): 869, (('S2',), ('Yp',)): 812, (('S2',), ('Ym',)): 819, ((

{'01': {(('S0',), ('Zp',)): 5008, (('S0',), ('Xp',)): 2537, (('S0',), ('Xm',)): 2478, (('S0',), ('Yp',)): 2536, (('S0',), ('Ym',)): 2457, (('S1',), ('Zp',)): 1653, (('S1',), ('Xp',)): 887, (('S1',), ('Xm',)): 834, (('S1',), ('Ym',)): 841, (('S1',), ('Yp',)): 772, (('S2',), ('Zp',)): 1641, (('S2',), ('Xm',)): 815, (('S2',), ('Xp',)): 884, (('S2',), ('Ym',)): 873, (('S2',), ('Yp',)): 813, (('S3',), ('Zp',)): 1646, (('S3',), ('Xm',)): 828, (('S3',), ('Xp',)): 852, (('S3',), ('Ym',)): 849, (('S3',), ('Yp',)): 837, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '11': {(('S0',), ('Zp',)): 4992, (('S0',), ('Xm',)): 2506, (('S0',), ('Xp',)): 2479, (('S0',), ('Yp',)): 2493, (('S0',), ('Ym',)): 2514, (('S1',), ('Zp',)): 1737, (('S1',), ('Xp',)): 862, (('S1',), ('Xm',)): 812, (('S1',), ('Ym',)): 839, (('S1',), ('Yp',)): 859, (('S2',), ('Zp',)): 1647, (('S2',), ('Xp',)): 868, (('S2',), ('Xm',)): 817, (('S2',), ('Yp',)): 815, (('S2',), ('Ym',)): 795, ((

{'01': {(('S0',), ('Zp',)): 10000, (('S0',), ('Xp',)): 4991, (('S0',), ('Xm',)): 5009, (('S0',), ('Ym',)): 5062, (('S0',), ('Yp',)): 4938, (('S1',), ('Zp',)): 3378, (('S1',), ('Xm',)): 1687, (('S1',), ('Xp',)): 1640, (('S1',), ('Yp',)): 1639, (('S1',), ('Ym',)): 1616, (('S2',), ('Zp',)): 3335, (('S2',), ('Xm',)): 1642, (('S2',), ('Xp',)): 1666, (('S2',), ('Ym',)): 1666, (('S2',), ('Yp',)): 1621, (('S3',), ('Zp',)): 3403, (('S3',), ('Xp',)): 1665, (('S3',), ('Xm',)): 1687, (('S3',), ('Ym',)): 1691, (('S3',), ('Yp',)): 1658, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '10': {(('S1',), ('Zp',)): 6622, (('S1',), ('Xp',)): 3395, (('S1',), ('Xm',)): 3278, (('S1',), ('Ym',)): 3429, (('S1',), ('Yp',)): 3316, (('S2',), ('Zp',)): 6665, (('S2',), ('Xp',)): 3328, (('S2',), ('Xm',)): 3364, (('S2',), ('Ym',)): 3456, (('S2',), ('Yp',)): 3257, (('S3',), ('Zp',)): 6597, (('S3',), ('Xp',)): 3288, (('S3',), ('Xm',)): 3360, (('S3',), ('Ym',)): 3323, (('S3',

In [85]:
# direct_models = ml.direct_fragment_model(frag_data)
# likely_models = ml.maximum_likelihood_model(direct_models)

# direct_recombined_dist = ml.recombine_fragment_models(direct_models, wire_path_map)
# likely_recombined_dist = ml.recombine_fragment_models(likely_models, wire_path_map)

In [86]:
from utils.utils import filter_results

In [87]:
filter_direct_recombined = filter_results(direct_recombined_dist, [0])

In [88]:

filter_likely_recombined = filter_results(likely_recombined_dist, [0])

In [89]:
norm_filter_dist = norm_dict(filter_likely_recombined)

In [90]:
final_expect_val = 0
for i in range(0, len(pauli_commute)):
    group = pauli_commute[i]
    for Pauli_tuple in group:
        coeff = Pauli_tuple[1]
        final_expect_val += coeff * evaluation(norm_filtered_lists[i], shots = total_counts(norm_filtered_lists[i]), Pauli = Pauli_tuple[0])  

In [91]:
final_expect_val

(-27.804710022328415+0j)

In [93]:
import json
with open('HF_auckland_check2.json', 'w') as f:
    json.dump(norm_filtered_lists, f)

In [94]:
mit = mthree.M3Mitigation(device)
mit.cals_from_file(cals_file = 'mit_data_9_8_14_11_13_12_10_7')

In [95]:
def update_dict(quasis, total_shots = None):
    for key in quasis.keys():
        quasis[key] = quasis[key]*total_shots

In [96]:
mit_lists = []
for i in range(0, len(pauli_commute)):
    total_shots = total_counts(norm_filtered_lists[i])
    quasis = mit.apply_correction(norm_filtered_lists[i], [9,8,14,11,13,12,10,7])
    update_dict(quasis, total_shots = total_shots)
    mit_lists.append(quasis)
miti_expect_val = 0
for i in range(0, len(pauli_commute)):
    group = pauli_commute[i]
    for Pauli_tuple in group:
        coeff = Pauli_tuple[1]
        miti_expect_val += coeff * evaluation(mit_lists[i], shots = total_counts(mit_lists[i]), Pauli = Pauli_tuple[0]) 
miti_expect_val

(-28.03048537102017+0j)

In [97]:
with open('HF_auckland_check2_mit.json', 'w') as f:
    json.dump(mit_lists, f)